In [1]:
!export CUDA_VISIBLE_DEVICES=2

In [2]:
import argparse
import glob
import logging
import os
import tqdm
import random

import numpy as np
import torch
from torch.utils.data import DataLoader, RandomSampler, SequentialSampler, TensorDataset
from torch.utils.data.distributed import DistributedSampler
from tqdm import tqdm, trange

from hans_processors import HansProcessor
from hans_processors import hans_convert_examples_to_features as convert_examples_to_features
from transformers import (
    WEIGHTS_NAME,
    AutoModelForSequenceClassification,
    AutoTokenizer,
)

In [3]:
from evaluate import create_eval_loader, predict, evaluate

In [4]:

model_path = "checkpoints/finetuned/"
device = torch.device("cuda:2")
hans_data_dir = "../../data/hans/"

# Other settings
max_seq_length = 128
batch_size = 256
model_type = "bert"

In [5]:
tokenizer = AutoTokenizer.from_pretrained(model_path)


In [6]:
eval_dataloader, label_list = create_eval_loader(data_dir=hans_data_dir, 
                                                 max_seq_length=max_seq_length, 
                                                 model_type=model_type, 
                                                 model_name_or_path=model_path, 
                                                 tokenizer=tokenizer, 
                                                 overwrite_cache=False, 
                                                 eval_batch_size=batch_size)

In [7]:
model = AutoModelForSequenceClassification.from_pretrained(model_path)
predictions = predict(device, model, tokenizer, eval_dataloader, label_list)
_ = evaluate(predictions, hans_data_dir)

Evaluating: 100%|██████████| 118/118 [01:12<00:00,  1.63it/s]


Heuristic entailed results:
lexical_overlap: 0.9102
subsequence: 0.9256
constituent: 0.9508

Entailed accuracy: 0.9288666666666666

Heuristic non-entailed results:
lexical_overlap: 0.1948
subsequence: 0.1156
constituent: 0.081

Non-Entailed accuracy: 0.13046666666666668

Overall accuracy: 0.5296666666666666

Subcase results:
ln_subject/object_swap: 0.097
ln_preposition: 0.339
ln_relative_clause: 0.218
ln_passive: 0.049
ln_conjunction: 0.271
le_relative_clause: 0.892
le_around_prepositional_phrase: 0.933
le_around_relative_clause: 0.963
le_conjunction: 0.871
le_passive: 0.892
sn_NP/S: 0.105
sn_PP_on_subject: 0.086
sn_relative_clause_on_subject: 0.029
sn_past_participle: 0.217
sn_NP/Z: 0.141
se_conjunction: 0.962
se_adjective: 1.0
se_understood_object: 0.894
se_relative_clause_on_obj: 0.928
se_PP_on_obj: 0.844
cn_embedded_under_if: 0.294
cn_after_if_clause: 0.035
cn_embedded_under_verb: 0.038
cn_disjunction: 0.025
cn_adverb: 0.013
ce_embedded_under_since: 0.813
ce_after_since_clause: 0.9

In [8]:
# Remove Layers

# Remove layers

In [19]:
from itertools import chain, combinations
def all_subsets(ss):
    return chain(*map(lambda x: combinations(ss, x), reversed(range(len(ss)+1))))

In [20]:


combinations = list(subset for subset in all_subsets(range(12)) if len(subset) == 9)
for subset_layers in tqdm(combinations):
    print(f"Subset: {subset_layers}")
    model = AutoModelForSequenceClassification.from_pretrained(model_path)
    model.bert.encoder.layer = torch.nn.ModuleList([l for i, l in enumerate(model.bert.encoder.layer) if i in subset_layers])
    predictions = predict(device, model, tokenizer, eval_dataloader, label_list)
    results = evaluate(predictions, hans_data_dir)
    layer_results[subset_layers] = results["accuracy"]
    if max_accuracy < results["accuracy"]:
        max_accuracy = results["accuracy"]
        print("MAX_ACCURACY", max_accuracy)





  0%|          | 0/220 [00:00<?, ?it/s]

Subset: (0, 1, 2, 3, 4, 5, 6, 7, 8)







Evaluating:   0%|          | 0/118 [00:00<?, ?it/s]




Evaluating:   1%|          | 1/118 [00:00<00:54,  2.15it/s]




Evaluating:   2%|▏         | 2/118 [00:00<00:54,  2.14it/s]




Evaluating:   3%|▎         | 3/118 [00:01<00:53,  2.16it/s]




Evaluating:   3%|▎         | 4/118 [00:01<00:52,  2.17it/s]




Evaluating:   4%|▍         | 5/118 [00:02<00:51,  2.18it/s]




Evaluating:   5%|▌         | 6/118 [00:02<00:51,  2.18it/s]




Evaluating:   6%|▌         | 7/118 [00:03<00:50,  2.19it/s]




Evaluating:   7%|▋         | 8/118 [00:03<00:50,  2.19it/s]




Evaluating:   8%|▊         | 9/118 [00:04<00:49,  2.19it/s]




Evaluating:   8%|▊         | 10/118 [00:04<00:49,  2.19it/s]




Evaluating:   9%|▉         | 11/118 [00:05<00:48,  2.19it/s]




Evaluating:  10%|█         | 12/118 [00:05<00:48,  2.19it/s]




Evaluating:  11%|█         | 13/118 [00:05<00:47,  2.19it/s]




Evaluating:  12%|█▏        | 14/118 [00:06<00:47,  2.19it/s]




Evaluating:  13%|█▎        | 15/118 [0

Heuristic entailed results:
lexical_overlap: 0.6134
subsequence: 0.866
constituent: 0.6572

Entailed accuracy: 0.7122

Heuristic non-entailed results:
lexical_overlap: 0.5502
subsequence: 0.4674
constituent: 0.4204

Non-Entailed accuracy: 0.47933333333333333

Overall accuracy: 0.5957666666666667

Subcase results:
ln_subject/object_swap: 0.509
ln_preposition: 0.715
ln_relative_clause: 0.59
ln_passive: 0.367
ln_conjunction: 0.57
le_relative_clause: 0.518
le_around_prepositional_phrase: 0.696
le_around_relative_clause: 0.81
le_conjunction: 0.738
le_passive: 0.305
sn_NP/S: 0.082
sn_PP_on_subject: 0.464
sn_relative_clause_on_subject: 0.48
sn_past_participle: 0.463
sn_NP/Z: 0.848
se_conjunction: 0.76
se_adjective: 0.962
se_understood_object: 0.892
se_relative_clause_on_obj: 0.948
se_PP_on_obj: 0.768
cn_embedded_under_if: 0.901
cn_after_if_clause: 0.139
cn_embedded_under_verb: 0.562
cn_disjunction: 0.364
cn_adverb: 0.136
ce_embedded_under_since: 0.178
ce_after_since_clause: 0.844
ce_embedded_






Evaluating:   0%|          | 0/118 [00:00<?, ?it/s]




Evaluating:   1%|          | 1/118 [00:00<00:56,  2.06it/s]




Evaluating:   2%|▏         | 2/118 [00:00<00:55,  2.09it/s]




Evaluating:   3%|▎         | 3/118 [00:01<00:54,  2.10it/s]




Evaluating:   3%|▎         | 4/118 [00:01<00:53,  2.12it/s]




Evaluating:   4%|▍         | 5/118 [00:02<00:53,  2.12it/s]




Evaluating:   5%|▌         | 6/118 [00:02<00:52,  2.13it/s]




Evaluating:   6%|▌         | 7/118 [00:03<00:52,  2.13it/s]




Evaluating:   7%|▋         | 8/118 [00:03<00:51,  2.13it/s]




Evaluating:   8%|▊         | 9/118 [00:04<00:51,  2.13it/s]




Evaluating:   8%|▊         | 10/118 [00:04<00:50,  2.13it/s]




Evaluating:   9%|▉         | 11/118 [00:05<00:50,  2.13it/s]




Evaluating:  10%|█         | 12/118 [00:05<00:49,  2.13it/s]




Evaluating:  11%|█         | 13/118 [00:06<00:49,  2.13it/s]




Evaluating:  12%|█▏        | 14/118 [00:06<00:48,  2.13it/s]




Evaluating:  13%|█▎        | 15/118 [0

...

Heuristic entailed results:
lexical_overlap: 0.7806
subsequence: 0.8774
constituent: 0.8544

Entailed accuracy: 0.8374666666666667

Heuristic non-entailed results:
lexical_overlap: 0.2224
subsequence: 0.1732
constituent: 0.1744

Non-Entailed accuracy: 0.19

Overall accuracy: 0.5137333333333334

Subcase results:
ln_subject/object_swap: 0.208
ln_preposition: 0.276
ln_relative_clause: 0.284
ln_passive: 0.194
ln_conjunction: 0.15
le_relative_clause: 0.764
le_around_prepositional_phrase: 0.721
le_around_relative_clause: 0.796
le_conjunction: 0.863
le_passive: 0.759
sn_NP/S: 0.033
sn_PP_on_subject: 0.203
sn_relative_clause_on_subject: 0.201
sn_past_participle: 0.177
sn_NP/Z: 0.252
se_conjunction: 0.901
se_adjective: 0.861
se_understood_object: 0.927
se_relative_clause_on_obj: 0.851
se_PP_on_obj: 0.847
cn_embedded_under_if: 0.195
cn_after_if_clause: 0.267
cn_embedded_under_verb: 0.138
cn_disjunction: 0.182
cn_adverb: 0.09
ce_embedded_under_since: 0.875
ce_after_since_clause: 0.758
ce_embedded






Evaluating:   0%|          | 0/118 [00:00<?, ?it/s]




Evaluating:   1%|          | 1/118 [00:00<00:55,  2.10it/s]




Evaluating:   2%|▏         | 2/118 [00:00<00:55,  2.10it/s]




Evaluating:   3%|▎         | 3/118 [00:01<00:54,  2.11it/s]




Evaluating:   3%|▎         | 4/118 [00:01<00:54,  2.11it/s]




Evaluating:   4%|▍         | 5/118 [00:02<00:53,  2.11it/s]




Evaluating:   5%|▌         | 6/118 [00:02<00:53,  2.11it/s]




Evaluating:   6%|▌         | 7/118 [00:03<00:52,  2.11it/s]




Evaluating:   7%|▋         | 8/118 [00:03<00:52,  2.11it/s]




Evaluating:   8%|▊         | 9/118 [00:04<00:51,  2.11it/s]




Evaluating:   8%|▊         | 10/118 [00:04<00:51,  2.11it/s]




Evaluating:   9%|▉         | 11/118 [00:05<00:50,  2.11it/s]




Evaluating:  10%|█         | 12/118 [00:05<00:50,  2.11it/s]




Evaluating:  11%|█         | 13/118 [00:06<00:49,  2.11it/s]




Evaluating:  12%|█▏        | 14/118 [00:06<00:49,  2.11it/s]




Evaluating:  13%|█▎        | 15/118 [0

Heuristic entailed results:
lexical_overlap: 0.8472
subsequence: 0.8564
constituent: 0.84

Entailed accuracy: 0.8478666666666667

Heuristic non-entailed results:
lexical_overlap: 0.1626
subsequence: 0.197
constituent: 0.169

Non-Entailed accuracy: 0.1762

Overall accuracy: 0.5120333333333333

Subcase results:
ln_subject/object_swap: 0.159
ln_preposition: 0.19
ln_relative_clause: 0.182
ln_passive: 0.13
ln_conjunction: 0.152
le_relative_clause: 0.855
le_around_prepositional_phrase: 0.803
le_around_relative_clause: 0.844
le_conjunction: 0.856
le_passive: 0.878
sn_NP/S: 0.022
sn_PP_on_subject: 0.238
sn_relative_clause_on_subject: 0.206
sn_past_participle: 0.14
sn_NP/Z: 0.379
se_conjunction: 0.85
se_adjective: 0.833
se_understood_object: 0.788
se_relative_clause_on_obj: 0.905
se_PP_on_obj: 0.906
cn_embedded_under_if: 0.176
cn_after_if_clause: 0.244
cn_embedded_under_verb: 0.161
cn_disjunction: 0.141
cn_adverb: 0.123
ce_embedded_under_since: 0.847
ce_after_since_clause: 0.748
ce_embedded_und






Evaluating:   0%|          | 0/118 [00:00<?, ?it/s]




Evaluating:   1%|          | 1/118 [00:00<00:56,  2.06it/s]




Evaluating:   2%|▏         | 2/118 [00:00<00:55,  2.08it/s]




Evaluating:   3%|▎         | 3/118 [00:01<00:55,  2.09it/s]




Evaluating:   3%|▎         | 4/118 [00:01<00:54,  2.09it/s]




Evaluating:   4%|▍         | 5/118 [00:02<00:53,  2.10it/s]




Evaluating:   5%|▌         | 6/118 [00:02<00:53,  2.11it/s]




Evaluating:   6%|▌         | 7/118 [00:03<00:52,  2.11it/s]




Evaluating:   7%|▋         | 8/118 [00:03<00:52,  2.11it/s]




Evaluating:   8%|▊         | 9/118 [00:04<00:51,  2.11it/s]




Evaluating:   8%|▊         | 10/118 [00:04<00:51,  2.11it/s]




Evaluating:   9%|▉         | 11/118 [00:05<00:50,  2.11it/s]




Evaluating:  10%|█         | 12/118 [00:05<00:50,  2.12it/s]




Evaluating:  11%|█         | 13/118 [00:06<00:49,  2.12it/s]




Evaluating:  12%|█▏        | 14/118 [00:06<00:49,  2.12it/s]




Evaluating:  13%|█▎        | 15/118 [0

Heuristic entailed results:
lexical_overlap: 0.8944
subsequence: 0.91
constituent: 0.919

Entailed accuracy: 0.9078

Heuristic non-entailed results:
lexical_overlap: 0.1066
subsequence: 0.111
constituent: 0.115

Non-Entailed accuracy: 0.11086666666666667

Overall accuracy: 0.5093333333333333

Subcase results:
ln_subject/object_swap: 0.103
ln_preposition: 0.15
ln_relative_clause: 0.16
ln_passive: 0.021
ln_conjunction: 0.099
le_relative_clause: 0.873
le_around_prepositional_phrase: 0.848
le_around_relative_clause: 0.884
le_conjunction: 0.895
le_passive: 0.972
sn_NP/S: 0.003
sn_PP_on_subject: 0.158
sn_relative_clause_on_subject: 0.142
sn_past_participle: 0.078
sn_NP/Z: 0.174
se_conjunction: 0.908
se_adjective: 0.841
se_understood_object: 0.939
se_relative_clause_on_obj: 0.948
se_PP_on_obj: 0.914
cn_embedded_under_if: 0.118
cn_after_if_clause: 0.166
cn_embedded_under_verb: 0.113
cn_disjunction: 0.092
cn_adverb: 0.086
ce_embedded_under_since: 0.952
ce_after_since_clause: 0.873
ce_embedded_u

In [23]:
layer_results

{(0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11): 0.5296666666666666,
 (0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10): 0.5225333333333333,
 (0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 11): 0.5524333333333333,
 (0, 1, 2, 3, 4, 5, 6, 7, 8, 10, 11): 0.5049,
 (0, 1, 2, 3, 4, 5, 6, 7, 9, 10, 11): 0.5255666666666666,
 (0, 1, 2, 3, 4, 5, 6, 8, 9, 10, 11): 0.5303333333333333,
 (0, 1, 2, 3, 4, 5, 7, 8, 9, 10, 11): 0.5251333333333333,
 (0, 1, 2, 3, 4, 6, 7, 8, 9, 10, 11): 0.5063333333333333,
 (0, 1, 2, 3, 5, 6, 7, 8, 9, 10, 11): 0.5156,
 (0, 1, 2, 4, 5, 6, 7, 8, 9, 10, 11): 0.5245666666666666,
 (0, 1, 3, 4, 5, 6, 7, 8, 9, 10, 11): 0.5183333333333333,
 (0, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11): 0.5384,
 (1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11): 0.5166333333333334,
 (0, 1, 2, 3, 4, 5, 6, 7, 8, 9): 0.5382333333333333,
 (0, 1, 2, 3, 4, 5, 6, 7, 8, 10): 0.5308666666666667,
 (0, 1, 2, 3, 4, 5, 6, 7, 8, 11): 0.5098333333333334,
 (0, 1, 2, 3, 4, 5, 6, 7, 9, 10): 0.5507,
 (0, 1, 2, 3, 4, 5, 6, 7, 9, 11): 0.5158666666666667,
 (0, 1, 2, 3, 4, 5, 6, 7

In [26]:
with open( "layer_removal_results.pkl", "wb") as f:
    pickle.dump(layer_results, f)